# La Palma 2021 Erruption data gathering and visualization

## Importing libraries

In [1]:
from datetime import datetime as dt
from datetime import timedelta

import pandas as pd
import numpy as np
import plotly.graph_objects as go
import plotly.express as px


from SeismicPortal.dl_quakes import CANARY_BOX, SeismicPortal

# sns.set_theme()
# sns.set(style="darkgrid")
# plt.rcParams['figure.figsize'] = [30, 15]

## Downloading latest eartquake data for the Canary Islands

In [2]:
sp = SeismicPortal()
# results = sp.download_earthquakes(start_time=dt.now() - timedelta(days=14), **CANARY_BOX)
results = sp.download_earthquakes(start_time=dt.now() - timedelta(days=60), **CANARY_BOX)

1905 earthquakes downloaded.


In [3]:
master_df = pd.DataFrame([q.get("properties") for q in results])

# Tranform data

# Remove timezone info to remove numpy deprecation warning
master_df["time"] = master_df["time"].apply(lambda x: x.strip("Z"))
master_df["lastupdate"] = master_df["lastupdate"].apply(lambda x: x.strip("Z"))

master_df["lastupdate"] = pd.to_datetime(master_df["lastupdate"])
master_df["time"] = pd.to_datetime(master_df["time"])
master_df["date"] = master_df["time"].dt.date

# Enhance data

# Create magnitude bins

m_bins = [
    pd.Interval(left=0, right=2),
    pd.Interval(left=2, right=3),
    pd.Interval(left=3, right=4),
    pd.Interval(left=4, right=5),
    pd.Interval(left=5, right=float("inf"))
]

# m_bins_small = [
#     pd.Interval(left=-float("inf"), right=3),
#     pd.Interval(left=3, right=float("inf")),
# ]

magnitude_ranges = []
for index, row in master_df.iterrows():
    for r in m_bins:
        if row["mag"] in r:
            magnitude_ranges.append(r)

master_df['mag_range'] = magnitude_ranges

# Auto create bins
# master_df['mag_range'] = pd.cut(master_df['mag'], bins = 5)

# Add mean magnitude and depth per day

master_df = pd.merge(master_df, master_df.groupby("date").mean().round(decimals=1)[["mag", "depth"]], on="date", suffixes=("", "_mean"), how="right")

master_df = pd.merge(master_df, master_df.groupby("date").size().reset_index(name='daily_eq'), how="left", on=["date"])


master_df = master_df.sort_values("time", ascending=False, ignore_index=True)
master_df


lastupdate magtype evtype    lon auth    lat  depth  \
0    2021-10-10 15:59:00      ml     ke -17.84  MDD  28.57   10.0   
1    2021-10-10 15:56:00      ml     ke -17.81  MDD  28.59   33.0   
2    2021-10-10 15:49:00      ml     ke -17.84  MDD  28.58    8.0   
3    2021-10-10 15:28:00      ml     ke -17.81  MDD  28.59   35.0   
4    2021-10-10 15:25:00      ml     ke -17.84  MDD  28.56   11.0   
...                  ...     ...    ...    ...  ...    ...    ...   
1900 2021-08-15 02:04:00      ml     ke -16.68  MDD  28.23   20.0   
1901 2021-08-14 23:29:00      ml     ke -16.32  MDD  28.30   12.0   
1902 2021-08-12 21:10:00      ml     ke -16.90  MDD  28.38    8.0   
1903 2021-08-12 05:41:00      ml     ke -16.25  MDD  28.16   22.0   
1904 2021-08-11 17:44:00      ml     ke -16.26  MDD  28.13   35.0   

                  unid  mag                    time source_id source_catalog  \
0     20211010_0000241  2.7 2021-10-10 15:55:46.700   1046671       EMSC-RTS   
1     20211010_0000240  2.6 2021-10-10 15:49:20.400   1046670       EMSC-RTS   
2     20211010_0000238  2.4 2021-10-10 15:39:40.100   1046667       EMSC-RTS   
3     20211010_0000231  3.4 2021-10-10 15:24:19.300   1046657       EMSC-RTS   
4     20211010_0000230  2.8 2021-10-10 15:21:04.400   1046656       EMSC-RTS   
...                ...  ...                     ...       ...            ...   
1900  20210815_0000014  1.6 2021-08-15 01:59:47.300   1023661       EMSC-RTS   
1901  20210814_0000325  1.6 2021-08-14 23:17:43.400   1023602       EMSC-RTS   
1902  20210812_0000243  1.5 2021-08-12 20:43:56.200   1022648       EMSC-RTS   
1903  20210812_0000062  1.8 2021-08-12 05:18:56.700   1022382       EMSC-RTS   
1904  20210811_0000155  2.1 2021-08-11 17:37:33.100   1022199       EMSC-RTS   

                      flynn_region        date mag_range  mag_mean  \
0     CANARY ISLANDS, SPAIN REGION  2021-10-10    (2, 3]       2.8   
1     CANARY ISLANDS, SPAIN REGION  2021-10-10    (2, 3]       2.8   
2     CANARY ISLANDS, SPAIN REGION  2021-10-10    (2, 3]       2.8   
3     CANARY ISLANDS, SPAIN REGION  2021-10-10    (3, 4]       2.8   
4     CANARY ISLANDS, SPAIN REGION  2021-10-10    (2, 3]       2.8   
...                            ...         ...       ...       ...   
1900  CANARY ISLANDS, SPAIN REGION  2021-08-15    (0, 2]       2.0   
1901  CANARY ISLANDS, SPAIN REGION  2021-08-14    (0, 2]       1.6   
1902  CANARY ISLANDS, SPAIN REGION  2021-08-12    (0, 2]       1.6   
1903  CANARY ISLANDS, SPAIN REGION  2021-08-12    (0, 2]       1.6   
1904  CANARY ISLANDS, SPAIN REGION  2021-08-11    (2, 3]       2.1   

      depth_mean  daily_eq  
0           19.2        92  
1           19.2        92  
2           19.2        92  
3           19.2        92  
4           19.2        92  
...          ...       ...  
1900        16.0         3  
1901        12.0         1  
1902        15.0         2  
1903        15.0         2  
1904        35.0         1  

[1905 rows x 18 columns]

## Visualization of data

In [4]:
df = master_df[master_df["time"] >= dt(2021, 9, 1)]


c_map = {
    pd.Interval(left=0, right=2): "rgb(255, 142, 37)",
    pd.Interval(left=2, right=3): "rgb(248, 67, 45)",
    pd.Interval(left=3, right=4): "rgb(217, 13, 57)",
    pd.Interval(left=4, right=5): "rgb(151, 2, 61)",
    pd.Interval(left=5, right=float("inf")): "rgb(49, 49, 49)",
}

# fig = px.histogram(df.sort_values("mag_range"), x="date", color="mag_range", barmode="group", color_discrete_sequence=px.colors.cyclical.IceFire)
fig = px.histogram(
    df.sort_values("mag_range"),
    x="date",
    color="mag_range", 
    barmode="group",
    color_discrete_map=c_map,
)
fig.show()

In [5]:
df = master_df[master_df["time"] >= dt(2021, 9, 28)]


fig = px.scatter(df, x="time", y=-df["depth"], color="mag", size=df["mag"] ** 2 , size_max=15, color_discrete_sequence=px.colors.cyclical.IceFire)
fig.show()

In [6]:
df = master_df[master_df["date"] < master_df.iloc[0].date]

fig = px.line(df, x="date", y="daily_eq")

fig.show()

In [7]:
df = master_df[master_df["time"] >= dt.now() - timedelta(days=45)]

fig = px.histogram(df, x="date", color="mag_mean", color_discrete_sequence=px.colors.sequential.thermal, nbins=46)
fig.show()

In [8]:
df = master_df[
    (master_df.lat <= 28.961) & 
    (master_df.lat >= 28.324) & 
    (master_df.lon <= -17.7935) & 
    (master_df.lon >= -17.9478) &
    (master_df.date > dt.now().date() - timedelta(days=14))
]

fig = px.scatter_3d(
    df, 
    x='lat',
    y='lon',
    z=-df['depth'], 
    color='mag',
    size=df['mag'] ** 2,
    labels={
        "z": "Depth (km)",
        "mag": "Magnitude",
    },
    title="3D plot of earthquakes depth"
)

fig.show()


In [9]:
print(f"This notebook was last updated: {dt.utcnow()} UTC")

This notebook was last updated: 2021-10-10 16:01:49.934251 UTC


## Donation

If you find this  useful please consider donating to one of my crypto account. Thank you :)

[![Donate](https://img.shields.io/badge/Donate-BTC-green.svg?style=plastic&logo=bitcoin)](https://raw.githubusercontent.com/Anonymous5726221/lapalma_data/master/Donate/BTC_Bitcoin)
[![Donate](https://img.shields.io/badge/Donate-BNB-green.svg?style=plastic&logo=binance)](https://raw.githubusercontent.com/Anonymous5726221/lapalma_data/master/Donate/BNB_BinanceSmartChain)
[![Donate](https://img.shields.io/badge/Donate-FTM-green.svg?style=plastic&logo=data:image/svg%2bxml;base64,PHN2ZyBjbGlwLXJ1bGU9ImV2ZW5vZGQiIGZpbGwtcnVsZT0iZXZlbm9kZCIgc3Ryb2tlLWxpbmVqb2luPSJyb3VuZCIgc3Ryb2tlLW1pdGVybGltaXQ9IjIiIHZpZXdCb3g9IjAgMCA1NjAgNDAwIiB4bWxucz0iaHR0cDovL3d3dy53My5vcmcvMjAwMC9zdmciPjxjaXJjbGUgY3g9IjI4MCIgY3k9IjIwMCIgZmlsbD0iIzEzYjVlYyIgcj0iMTUwIiBzdHJva2Utd2lkdGg9IjkuMzc1Ii8+PHBhdGggZD0ibTE3LjIgMTIuOSAzLjYtMi4xdjQuMnptMy42IDktNC44IDIuOC00LjgtMi44di00LjlsNC44IDIuOCA0LjgtMi44em0tOS42LTExLjEgMy42IDIuMS0zLjYgMi4xem01LjQgMy4xIDMuNiAyLjEtMy42IDIuMXptLTEuMiA0LjItMy42LTIuMSAzLjYtMi4xem00LjgtOC4zLTQuMiAyLjQtNC4yLTIuNCA0LjItMi41em0tMTAuMi0uNHYxMy4xbDYgMy40IDYtMy40di0xMy4xbC02LTMuNHoiIGZpbGw9IiNmZmYiIHRyYW5zZm9ybT0ibWF0cml4KDkuMzc1IDAgMCA5LjM3NSAxMzAgNTApIi8+PC9zdmc+)](https://raw.githubusercontent.com/Anonymous5726221/lapalma_data/master/Donate/FTM_Fantom)